## Парсинг данных с сайта на Python

### Определения

Парсинг - это процесс сбора данных с последующей их обработкой и анализом.

Программа, которая занимается парсингом, называют - парсер.


### Условие задачи

С сайта ( https://habr.com/ru/search/ ) необходимо построить исходный набор данных (.csv или .xml). Набор данных должен включать __названия, описание, рейтинг и сферу деятельности компаний, дату публикации, а также текст статей из Интернет-ресурсов__. Подготовленный набор данных должен содержать сведения о всех номинантах конкурса. Разработанный парсер должен извлекать гиперссылки из начальной страницы с последующим обходом всех страниц по полученным ссылкам и извлечением их содержимого. Можно дополнить набор какими-либо другими данными, если они могут быть полезны для дальнейшего исследования.


### Этапы парсинга

1. Поиск данных
2. Получение информации
3. Сохранение данных

### Подключение библиотек

In [29]:
from bs4 import BeautifulSoup as bs

Beautiful Soup - это библиотека Python для извлечения данных из HTML и XML файлов. 

In [32]:
import requests

Библиотека requests является стандартным инструментом для составления HTTP-запросов в Python.

In [34]:
import pandas as pd

### Получение информаций

In [36]:
# GET - запрос
url = 'https://habr.com/ru/all/' # страница со всеми статьями 
page = requests.get(url)

Метод __requests.get(url)__ из библиотеки requests в Python выполняет HTTP-запрос типа GET по указанному URL. Этот запрос используется для получения данных с веб-страницы или API, в нашем случае из страницы habr.

In [38]:
page.status_code

200

Если вызвать __page.status_code__, то получим статус состояния HTTP. например, 200 — успешно, 404 — страница не найдена, 500 — ошибка сервера 


In [40]:
soup = bs(page.text, 'html.parser')

__bs__ — это сокращение от BeautifulSoup, основного класса библиотеки Beautiful Soup.

__bs(page.text, 'html.parser')__ создаёт объект BeautifulSoup, который парсит HTML-код из page.text с использованием указанного парсера.

__'html.parser'__ — это встроенный парсер Python, который не требует установки дополнительных библиотек.а.

In [44]:
page.text

'<!DOCTYPE html>\n<html lang="ru">\n\n  <head>\n    <title>Все статьи подряд &#x2F; Хабр</title>\n<link rel="image_src" href="/img/habr_ru.png" data-hid="2a79c45">\n<link href="https://habr.com/ru/articles/" rel="canonical" data-hid="e3fa780">\n<link href="https://habr.com/ru/articles/" hreflang="ru" rel="alternate" data-hid="7d51b8a">\n<link href="https://habr.com/en/articles/" hreflang="en" rel="alternate" data-hid="7d51b8a">\n<meta itemprop="image" content="/img/habr_ru.png">\n<meta property="og:image" content="/img/habr_ru.png">\n<meta property="og:image:width" content="1200">\n<meta property="og:image:height" content="630">\n<meta property="aiturec:image" content="/img/habr_ru.png">\n<meta name="twitter:image" content="/img/habr_ru.png">\n<meta property="vk:image" content="/img/habr_ru.png?format=vk">\n<meta property="fb:app_id" content="444736788986613">\n<meta property="fb:pages" content="472597926099084">\n<meta name="twitter:card" content="summary_large_image">\n<meta name="tw

In [45]:
soup

<!DOCTYPE html>

<html lang="ru">
<head>
<title>Все статьи подряд / Хабр</title>
<link data-hid="2a79c45" href="/img/habr_ru.png" rel="image_src"/>
<link data-hid="e3fa780" href="https://habr.com/ru/articles/" rel="canonical"/>
<link data-hid="7d51b8a" href="https://habr.com/ru/articles/" hreflang="ru" rel="alternate"/>
<link data-hid="7d51b8a" href="https://habr.com/en/articles/" hreflang="en" rel="alternate"/>
<meta content="/img/habr_ru.png" itemprop="image"/>
<meta content="/img/habr_ru.png" property="og:image"/>
<meta content="1200" property="og:image:width"/>
<meta content="630" property="og:image:height"/>
<meta content="/img/habr_ru.png" property="aiturec:image"/>
<meta content="/img/habr_ru.png" name="twitter:image"/>
<meta content="/img/habr_ru.png?format=vk" property="vk:image"/>
<meta content="444736788986613" property="fb:app_id"/>
<meta content="472597926099084" property="fb:pages"/>
<meta content="summary_large_image" name="twitter:card"/>
<meta content="@habr_com" name=

Создадим словарь, в который будем записывать данные по заданию: название статьи, описание, рейтинг и сферу деятельности компаний, дату публикации, а также текст статьи из Интернет-ресурса

In [96]:

result_list = {'title': [], 'namecompany': [], 'description': [], 'rating': [], 'field': [], 'date': [], 'textpub': [], 'views': []}

### Алгоритм

Суть алгоритма заключается в переборе страниц, и переходе на "вложенные" страницы, то есть у нас есть основная страница https://habr.com/ru/all/, мы перебираем несколько стараниц с page1 до page10. На каждой странице есть статьи, записываем их в список, чтобы перейти по ним используем  _-i.a.get('href')-_  то есть берём значение из href этого заголовка. Далее находим классы элементов которые нам нужны, и записываем их в результат.

In [160]:
pagenum = 1
for i in range(10):
    url = 'https://habr.com/ru/articles/page' + str(pagenum) + '/' # переход на ссылуку с определённым номером сраницы
    page = requests.get(url)
    soup = bs(page.text, 'html.parser')
    titles = soup.find_all('h2', class_='tm-title tm-title_h2')# получаем заголовки всех статей на этой странице
    
    for i in titles: 
        # переход на страницу статьи
        url = 'https://habr.com' + str(i.a.get('href')) 
        page = requests.get(url)
        soup = bs(page.text, 'html.parser')
        
        name_company = soup.find('a', class_='tm-company-snippet__title')# получаем название компаний
        desc_company = soup.find('div', class_='tm-company-snippet__description')# получаем описание компаний
        
        if (name_company is not None): #если на странице присутсвует компания
        
            result_list['title'].append(i.text) # записываем название статьи
            result_list['namecompany'].append(name_company.text) # записываем название компании
            result_list['description'].append(desc_company.text) # записываем описание компании
            
            datepub = soup.find('span', class_='tm-article-datetime-published') # находим дату публикаций
            result_list['date'].append(datepub.time['datetime'][0: 10]) # записываем дату публикаций
            
            # текст статьи
            try:
                textpub = soup.find('div', class_='article-formatted-body article-formatted-body article-formatted-body_version-2').get_text()
                textpub = textpub.replace('\n', ' ').replace('\t', ' ').replace('\xa0', ' ').replace('\u200e', ' ').replace('\r', ' ')
            except:
                textpub = soup.find('div', class_='article-formatted-body article-formatted-body article-formatted-body_version-1').get_text()
                textpub = textpub.replace('\n', ' ').replace('\t', ' ').replace('\xa0', ' ').replace('\u200e', ' ').replace('\r', ' ')
            result_list['textpub'].append(textpub)
            
            # переход на страницу компании
            url = 'https://habr.com' + str(name_company.get('href'))
            page = requests.get(url)
            soup = bs(page.text, 'html.parser')
            
            #записываем рейтинг
            rating = soup.find('span', class_='tm-votes-lever__score-counter tm-votes-lever__score-counter_rating tm-votes-lever__score-counter')
            if(rating is None):
                result_list['rating'].append('0')
            else:
                result_list['rating'].append((rating.text).strip())
               
             #записываем отрасли компаний
            fieldtext = ""
            fields = soup.find_all('a', 'tm-company-profile__categories-text')
            for field in fields:
                fieldtext = fieldtext + ((field.text).strip()) + ", "
            if (fields is None):
                result_list['field'].append(None)
            else:
                result_list['field'].append(fieldtext[0:-2])
            result_list['views'].append('None')
            
    pagenum += 1

In [161]:
result_list

{'title': ['Как мы челленджим бизнес в GenAI: от простых Naive RAG до workflow-агентских систем',
  'Как настроить резервирование VK Private Cloud с помощью RuBackup',
  'Русский след в истории логотипа PostgreSQL',
  'Месяц с Nintendo 2DS: последняя великая портативка',
  'Как сократить время сборки с помощью кеширования контекста от Spring Test',
  'Заплатки для LAG/LEAD',
  'Crypters And Tools. Часть 2: Разные лапы — один клубок',
  'Внедрение Битрикс24 в концертную деятельность зала «Зарядье»',
  'Как я проектировал телескопическую трибуну, используя параметризацию в КОМПАС-3D',
  'Как мы создавали K-Team HRM: тернистый путь от консалтинга к продукту',
  'Модель датчика энтропии из веток и шишек',
  '15 лет назад такого не было. Что случилось с телефоном, автомобилем и кардиостимулятором',
  'Какие главные изменения в сфере интеллектуальной собственности? Отвечает CEO Онлайн Патента',
  'Эволюция хранилища ВКонтакте: от первой реализации до наших дней',
  'Книга: «RESTful Web API: 

In [162]:
print("Количество нулевых значений в: ")
for i in result_list:
    print( i + " - " + str(result_list[i].count(None)))

Количество нулевых значений в: 
title - 0
namecompany - 0
description - 0
rating - 0
field - 0
date - 0
textpub - 0
views - 0


### Сохранение данных

In [164]:
file_name = 'habr.csv'
df = pd.DataFrame(data=result_list)
df.to_csv(file_name)

In [165]:
df.head()

title            namecompany  \
0  Как мы челленджим бизнес в GenAI: от простых N...          red_mad_robot   
1  Как настроить резервирование VK Private Cloud ...           Группа Астра   
2         Русский след в истории логотипа PostgreSQL  Postgres Professional   
3  Месяц с Nintendo 2DS: последняя великая портат...              RUVDS.com   
4  Как сократить время сборки с помощью кеширован...             Spring АйО   

                                    description   rating  \
0  №1 в разработке цифровых решений для бизнеса    98.83   
1                                      Компания    106.6   
2                 Разработчик СУБД Postgres Pro   262.32   
3    VDS/VPS-хостинг. Скидка 15% по коду HABR15  3310.15   
4                                      Компания    220.9   

                                               field        date  \
0  Программное обеспечение, Дизайн и юзабилити, М...  2025-04-29   
1  Программное обеспечение, Аппаратное обеспечени...  2025-04-29   
2  Программное обеспечение, Консалтинг и поддержк...  2025-04-29   
3  Связь и телекоммуникации, Домены и хостинг, Ве...  2025-04-29   
4                            Программное обеспечение  2025-04-29   

                                             textpub views  
0  Привет! На связи Валера Ковальский — руководит...  None  
1  ДисклеймерЭкосистема «Группы Астра» включа ет ...  None  
2  Об истории логотипа PostgreSQL рассказал генер...  None  
3   Сегодня консоли Nintendo 3/2DS с теплотой всп...  None  
4  Новый перевод от команды Spring АйО расскажет ...  None

In [166]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 207 entries, 0 to 206
Data columns (total 8 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   title        207 non-null    object
 1   namecompany  207 non-null    object
 2   description  207 non-null    object
 3   rating       207 non-null    object
 4   field        207 non-null    object
 5   date         207 non-null    object
 6   textpub      207 non-null    object
 7   views        207 non-null    object
dtypes: object(8)
memory usage: 13.1+ KB


In [1]:
import fitz

In [168]:
def extract_text_from_pdf(pdf_path):
    try:
        doc = fitz.open(pdf_path)
        text = ''
        for page in doc:
            text += page.get_text("text")
        return text
    except Exception as e:
        print(f"Ошибка чтения {pdf_path}: {e}")
        return ""

In [169]:
def parse_pdf(text):
    # Ищем заголовок статьи
    title_match = re.search(r'(Ускоритель NICA в действии)', text)
    title = title_match.group(1) if title_match else 'Неизвестно'
    
    # Ищем компанию
    company_match = re.search(r'(CatNews @\w+)', text)
    namecompany = company_match.group(1) if company_match else ''
    
    # Поиск рейтинга
    rating_match = re.search(r'([+-]?\d+(?:\.\d+)?)', text)
    rating = rating_match.group(1) if rating_match else ''
    
    # Поиск даты
    date_match = re.search(r'(\d{1,2} \w+ в \d{1,2}:\d{2})', text)
    date = date_match.group(1) if date_match else ''
    
    # Весь текст статьи
    textpub = text[:1000]
    
    description = ''
    lines = text.split('\n')
    if len(lines) > 3:
        description = ' '.join(lines[:3])
    else:
        description = text[:50]
    
    return {
        'title': title,
        'namecompany': 'CatNews',
        'description': description,
        'rating': rating,
        'field': None,
        'date': date,
        'textpub': textpub
    }

In [170]:
pdf_path = r'C:\Users\romad\Parsing\Ускоритель NICA в действии _ Хабр.pdf'
pdf_text = extract_text_from_pdf(pdf_path)
pdf_data = parse_pdf(pdf_text)

In [181]:
df_new = pd.DataFrame([pdf_data])
df = pd.concat([df, df_new], ignore_index=True)

In [183]:
df.head()

title            namecompany  \
0  Как мы челленджим бизнес в GenAI: от простых N...          red_mad_robot   
1  Как настроить резервирование VK Private Cloud ...           Группа Астра   
2         Русский след в истории логотипа PostgreSQL  Postgres Professional   
3  Месяц с Nintendo 2DS: последняя великая портат...              RUVDS.com   
4  Как сократить время сборки с помощью кеширован...             Spring АйО   

                                    description   rating  \
0  №1 в разработке цифровых решений для бизнеса    98.83   
1                                      Компания    106.6   
2                 Разработчик СУБД Postgres Pro   262.32   
3    VDS/VPS-хостинг. Скидка 15% по коду HABR15  3310.15   
4                                      Компания    220.9   

                                               field        date  \
0  Программное обеспечение, Дизайн и юзабилити, М...  2025-04-29   
1  Программное обеспечение, Аппаратное обеспечени...  2025-04-29   
2  Программное обеспечение, Консалтинг и поддержк...  2025-04-29   
3  Связь и телекоммуникации, Домены и хостинг, Ве...  2025-04-29   
4                            Программное обеспечение  2025-04-29   

                                             textpub views  
0  Привет! На связи Валера Ковальский — руководит...  None  
1  ДисклеймерЭкосистема «Группы Астра» включа ет ...  None  
2  Об истории логотипа PostgreSQL рассказал генер...  None  
3   Сегодня консоли Nintendo 3/2DS с теплотой всп...  None  
4  Новый перевод от команды Spring АйО расскажет ...  None

In [185]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 208 entries, 0 to 207
Data columns (total 8 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   title        208 non-null    object
 1   namecompany  208 non-null    object
 2   description  208 non-null    object
 3   rating       208 non-null    object
 4   field        207 non-null    object
 5   date         208 non-null    object
 6   textpub      208 non-null    object
 7   views        207 non-null    object
dtypes: object(8)
memory usage: 13.1+ KB


In [187]:
df.head(209)

title            namecompany  \
0    Как мы челленджим бизнес в GenAI: от простых N...          red_mad_robot   
1    Как настроить резервирование VK Private Cloud ...           Группа Астра   
2           Русский след в истории логотипа PostgreSQL  Postgres Professional   
3    Месяц с Nintendo 2DS: последняя великая портат...              RUVDS.com   
4    Как сократить время сборки с помощью кеширован...             Spring АйО   
..                                                 ...                    ...   
203  Jetpack Compose для Android TV: как происходит...                    МТС   
204  В центре внимания Java: Local Variable Type In...              Axiom JDK   
205  Первые вызовы и много шуток: что скрыто в бесп...       Яндекс Практикум   
206                          Мой путь к удаленке в Гоа          Online patent   
207                         Ускоритель NICA в действии                CatNews   

                                           description   rating  \
0         №1 в разработке цифровых решений для бизнеса    98.83   
1                                             Компания    106.6   
2                        Разработчик СУБД Postgres Pro   262.32   
3           VDS/VPS-хостинг. Скидка 15% по коду HABR15  3310.15   
4                                             Компания    220.9   
..                                                 ...      ...   
203                          Про жизнь и развитие в IT  2176.69   
204                        на страже безопасности Java    75.81   
205                               Помогаем людям расти   110.94   
206                          Ваш личный патентный офис   294.67   
207  Месяц назад, а именно 25 марта, в Дубне на уск...       25   

                                                 field            date  \
0    Программное обеспечение, Дизайн и юзабилити, М...      2025-04-29   
1    Программное обеспечение, Аппаратное обеспечени...      2025-04-29   
2    Программное обеспечение, Консалтинг и поддержк...      2025-04-29   
3    Связь и телекоммуникации, Домены и хостинг, Ве...      2025-04-29   
4                              Программное обеспечение      2025-04-29   
..                                                 ...             ...   
203  Связь и телекоммуникации, Мобильные технологии...      2025-04-28   
204  Программное обеспечение, Консалтинг и поддержк...      2025-04-28   
205                        Веб-разработка, Веб-сервисы      2025-04-28   
206                Консалтинг и поддержка, Веб-сервисы      2025-04-28   
207                                               None  26 апр в 18:30   

                                               textpub views  
0    Привет! На связи Валера Ковальский — руководит...  None  
1    ДисклеймерЭкосистема «Группы Астра» включа ет ...  None  
2    Об истории логотипа PostgreSQL рассказал генер...  None  
3     Сегодня консоли Nintendo 3/2DS с теплотой всп...  None  
4    Новый перевод от команды Spring АйО расскажет ...  None  
..                                                 ...   ...  
203  Привет, Хабр! Меня зовут Сергей Захаров, я раз...  None  
204  Команда Axiom JDK подготовила перевод статьи п...  None  
205  Привет! Это команда Яндекс Практикума. Первые ...  None  
206  закат в АрамболеПривет, Habr! Меня зовут Ксени...  None  
207  Месяц назад, а именно 25 марта, в Дубне на уск...   NaN  

[208 rows x 8 columns]